In [1]:
import numpy as np
import os
import time
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import math
import random

MIN_LIST_LEN = 14
MAX_LIST_LEN = 14
MAX_STEPS = 512

SUCCESS_REWARD = 2.0
STEP_REWARD = -0.1
SWAP_REWARD = 1.0
INVALID_ACTION_REWARD = -10.0

EPS_START = 0.5
EPS_END = 0.05
EPS_DECAY = 1000
GAMMA = 0.8
NUM_EPISODES = 100000
EPISODES_SAVE = 1000
OUTPUT_DIR = 'datasets/rl_sort_transformer_easy/list14_transformer5_256_gamma08_step512_v1'

# Define the vocabulary
vocab = {
    'Comparison': 0,
    'Swap': 1,
    'less': 2,
    'equal': 3,
    'more': 4,
    '0': 5,
    '1': 6,
    '2': 7,
    '3': 8,
    '4': 9,
    '5': 10,
    '6': 11,
    '7': 12,
    '8': 13,
    '9': 14,
    '10': 15,
    '11': 16,
    '12': 17,
    '13': 18,
    '14': 19,
    '15': 20,
    'len1': 21,
    'len2': 22,
    'len3': 23,
    'len4': 24,
    'len5': 25,
    'len6': 26,
    'len7': 27,
    'len8': 28,
    'len9': 29,
    'len10': 30,
    'len11': 31,
    'len12': 32,
    'len13': 33,
    'len14': 34,
    'len15': 35,
    'len16': 36,
}
inv_vocab = {v: k for k, v in vocab.items()}

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Define the environment
class SortingEnv:
    def __init__(self):
        self.max_steps = MAX_STEPS

    def reset(self):
        self.length = random.randint(MIN_LIST_LEN, MAX_LIST_LEN)
        self.list = [random.randint(1, 100) for _ in range(self.length)]
        while self.list == sorted(self.list):
            self.list = [random.randint(1, 100) for _ in range(self.length)]
        self.indices = None
        self.current_step = 0
        self.done = False
        initial_token = 'len{}'.format(self.length)
        return vocab[initial_token], self.list.copy()
    
    def get_list(self):
        return self.list
    
    def get_list_len(self):
        return len(self.list)

    def step(self, action_tokens):
        action = action_tokens[0]
        reward = -0.01  # default penalty
        response_token = None

        if action == vocab['Comparison']:
            if len(action_tokens) != 3:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1 = action_tokens[1] - vocab['0']
            index2 = action_tokens[2] - vocab['0']
            if index1 >= self.length or index2 >= self.length or index1 < 0 or index2 < 0:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            self.indices = (index1, index2)
            if self.list[index1] < self.list[index2]:
                response_token = vocab['less']
                reward = STEP_REWARD
            elif self.list[index1] == self.list[index2]:
                response_token = vocab['equal']
                reward = STEP_REWARD * 2
            else:
                response_token = vocab['more']
                reward = STEP_REWARD
        elif action == vocab['Swap']:
            if self.indices is None:
                reward = INVALID_ACTION_REWARD
                self.done = True
                return response_token, reward, self.done, self.list.copy()
            index1, index2 = self.indices
            prev_list = self.list.copy()
            self.list[index1], self.list[index2] = self.list[index2], self.list[index1]
            if self.list == sorted(self.list):
                reward = SUCCESS_REWARD
                self.done = True
            #elif prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]:
            #    reward = 0.1
            elif (index1 < index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]):
                reward = SWAP_REWARD
            elif (index1 < index2 and prev_list[index1] < prev_list[index2] and self.list[index1] >= self.list[index2]) or \
                (index1 > index2 and prev_list[index1] > prev_list[index2] and self.list[index1] <= self.list[index2]):
                reward = -SWAP_REWARD
            else:
                reward = STEP_REWARD
            self.indices = None
        else:
            reward = INVALID_ACTION_REWARD
            self.done = True

        self.current_step += 1
        if self.current_step >= self.max_steps:
            self.done = True
        return response_token, reward, self.done, self.list.copy()


Using device: cuda


In [2]:
# Positional Encoding for Transformer
class PositionalEncoding(nn.Module):
    def __init__(self, d_model, max_len=512):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=0.1)

        pe = torch.zeros(max_len, d_model)  # (max_len, d_model)
        position = torch.arange(0, max_len, dtype=torch.float).unsqueeze(1)  # (max_len, 1)
        div_term = torch.exp(torch.arange(0, d_model, 2).float() *
                             (-math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)  # Even indices
        pe[:, 1::2] = torch.cos(position * div_term)  # Odd indices
        pe = pe.unsqueeze(1)  # (max_len, 1, d_model)
        self.register_buffer('pe', pe)

    def forward(self, x):
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)

# Transformer Model
class TransformerModel(nn.Module):
    def __init__(self, vocab_size, d_model=256, nhead=8, num_layers=5):
        super(TransformerModel, self).__init__()
        self.model_type = 'Transformer'
        self.d_model = d_model

        self.embedding = nn.Embedding(vocab_size, d_model)
        self.pos_encoder = PositionalEncoding(d_model)
        encoder_layers = nn.TransformerEncoderLayer(d_model, nhead)
        self.transformer_encoder = nn.TransformerEncoder(encoder_layers, num_layers)
        self.decoder = nn.Linear(d_model, vocab_size)

        self.init_weights()

    def init_weights(self):
        initrange = 0.1
        nn.init.uniform_(self.embedding.weight, -initrange, initrange)
        nn.init.zeros_(self.decoder.bias)
        nn.init.uniform_(self.decoder.weight, -initrange, initrange)

    def forward(self, src):
        src = self.embedding(src) * math.sqrt(self.d_model)
        src = self.pos_encoder(src)
        output = self.transformer_encoder(src)
        output = self.decoder(output)
        return output

def decode(input_tokens, inv_vocab):
    return ' '.join([inv_vocab[x] for x in input_tokens])


def save_checkpoint(model, optimizer, episode, folder, filename):
    """
    Save the model and optimizer state to the designated filepath.

    Args:
        model (nn.Module): The model to save.
        optimizer (torch.optim.Optimizer): The optimizer whose state to save.
        episode (int): The current episode number.
        filepath (str): The path where to save the checkpoint.
    """
    filepath = os.path.join(folder, filename)
    # Ensure the directory exists
    os.makedirs(os.path.dirname(filepath), exist_ok=True)
    # Save the checkpoint
    torch.save({
        'episode': episode,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
    }, filepath)
    print(f"Checkpoint saved at episode {episode} to {filepath}")

def load_checkpoint(filepath, model, optimizer):
    """
    Load the model and optimizer state from the designated filepath.

    Args:
        filepath (str): The path from where to load the checkpoint.
        model (nn.Module): The model into which to load the state_dict.
        optimizer (torch.optim.Optimizer): The optimizer into which to load the state.

    Returns:
        int: The episode number to resume from.
    """
    if os.path.isfile(filepath):
        checkpoint = torch.load(filepath, map_location=device)
        model.load_state_dict(checkpoint['model_state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        episode = checkpoint['episode']
        print(f"Checkpoint loaded from {filepath}, resuming from episode {episode}")
        return episode
    else:
        print(f"No checkpoint found at {filepath}, starting from scratch.")
        return 0

In [ ]:
# Training Loop
def train(verbose=False):
    # Removed torch.autograd.set_detect_anomaly(True)
    vocab_size = len(vocab)
    model = TransformerModel(vocab_size).to(device)
    optimizer = optim.Adam(model.parameters(), lr=1e-4)  # Reduced learning rate
    # Optionally, load a checkpoint
    # load_checkpoint("path_to_checkpoint", model, optimizer)

    episode_cnt = 0
    total_reward = 0.0
    num_successes = 0
    total_steps = 0
    
    for episode in range(NUM_EPISODES):
        t1 = time.time()
        model.train()  # Set model to training mode
        env = SortingEnv()
        initial_token_id, current_list = env.reset()
        input_tokens = [initial_token_id]
        log_probs = []
        rewards = []
        
        state = 'expect_action'
        done = False
        success = False

        while not done and len(input_tokens) < env.max_steps:
            if verbose:
                print(decode(input_tokens, inv_vocab))
                print(env.get_list())
            # Prepare input tensor
            input_seq = torch.tensor(input_tokens, dtype=torch.long, device=device).unsqueeze(1)  # (seq_len, batch_size)
            # Get model output
            with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
                output = model(input_seq)  # (seq_len, batch_size, vocab_size)
                # Get logits for the last token
                logits = output[-1, 0, :]  # (vocab_size)

                # Check for NaNs in logits
                if torch.isnan(logits).any():
                    print(f"Episode {episode}, NaNs in logits before masking.")
                    break

                # Get valid tokens based on state
                def get_valid_tokens(state):
                    action_tokens = [vocab['Comparison'], vocab['Swap']]
                    index_tokens = [vocab[str(i)] for i in range(env.length)]
                    if state == 'expect_action':
                        return action_tokens
                    elif state == 'expect_index1':
                        return index_tokens[:-1]
                    elif state == 'expect_index2':
                        return [x for x in index_tokens if x > input_tokens[-1]]
                    else:
                        # Handle unexpected states by defaulting to expect_action
                        return action_tokens

                valid_token_ids = get_valid_tokens(state)

                # Ensure valid_token_ids are within the vocab range
                if any(idx >= vocab_size or idx < 0 for idx in valid_token_ids):
                    print(f"Episode {episode}, invalid indices in valid_token_ids: {valid_token_ids}")
                    break

                # Mask invalid tokens
                mask_value = -1e9  # Use a large negative value instead of -inf
                mask = torch.full_like(logits, mask_value).to(device)
                mask[valid_token_ids] = 0
                masked_logits = logits + mask

                # Sample action. Have some chance to randomly pick a valid action.
                eps_threshold = EPS_END + (EPS_START - EPS_END) * np.exp(-1.0 * episode / EPS_DECAY)
                if random.random() < eps_threshold:
                    masked_logits = masked_logits / 4

                # Check for NaNs in masked_logits
                if torch.isnan(masked_logits).any():
                    print(f"Episode {episode}, NaNs in masked_logits after masking.")
                    break

                # Compute probabilities
                probs = F.softmax(masked_logits, dim=0)

                # Check for NaNs in probs
                if torch.isnan(probs).any():
                    print(f"Episode {episode}, NaNs in probs after softmax.")
                    break

                try:
                    m = torch.distributions.Categorical(probs)
                    action_token = m.sample()
                    log_prob = m.log_prob(action_token)
                except ValueError as e:
                    print(f"Episode {episode}, error in sampling action: {e}")
                    break

            log_probs.append(log_prob)
            input_tokens.append(action_token.item())

            action = action_token.item()
            reward = 0.0
            if state == 'expect_action':
                if action == vocab['Comparison']:
                    state = 'expect_index1'
                elif action == vocab['Swap']:
                    if env.indices is None:
                        reward = INVALID_ACTION_REWARD
                        rewards.append(reward)
                        done = True
                        continue
                    action_tokens = [vocab['Swap']]
                    response_token, reward, done, current_list = env.step(action_tokens)
                    if done and reward == SUCCESS_REWARD:
                        success = True
                    if verbose:
                        print("Reward:", reward)
                    state = 'expect_action'
                else:
                    reward = INVALID_ACTION_REWARD
                    done = True
            elif state == 'expect_index1':
                index1_token = action_token
                state = 'expect_index2'
            elif state == 'expect_index2':
                index2_token = action_token
                action_tokens = [vocab['Comparison'], index1_token.item(), index2_token.item()]
                response_token, reward, done, current_list = env.step(action_tokens)
                if done and reward == SUCCESS_REWARD:
                    success = True
                if verbose:
                    print("Reward:", reward)
                if response_token is not None:
                    input_tokens.append(response_token)
                state = 'expect_action'
            else:
                reward = INVALID_ACTION_REWARD
                done = True

            rewards.append(reward)
        #
        if success: 
            num_successes += 1
        # Save checkpoint
        if episode > 0 and episode % EPISODES_SAVE == 0:
            avg_reward = total_reward / episode_cnt
            success_rate = num_successes / episode_cnt
            avg_steps = total_steps / episode_cnt
            episode_cnt = 0
            total_reward = 0.0
            num_successes = 0
            total_steps = 0
            save_checkpoint(model, optimizer, episode, OUTPUT_DIR, f"ckpt_{episode}_{success_rate:.4f}_{avg_steps:.2f}.pth")
        #
        assert len(log_probs) == len(rewards), "log_probs and returns have different sizes!"

        if len(log_probs) == 0:
            continue  # Skip if no actions were taken

        # Compute returns and loss within autocast
        with torch.autocast(device_type=device.type, dtype=torch.bfloat16):
            # Compute returns
            returns = []
            R = 0
            gamma = GAMMA
            for r in rewards[::-1]:
                R = r + gamma * R
                returns.insert(0, R)
            returns = torch.tensor(returns).to(device)

            # Check for NaNs in returns
            if torch.isnan(returns).any():
                print(f"Episode {episode}, NaNs in returns.")
                continue

            # Compute loss
            loss = 0
            for log_prob, R in zip(log_probs, returns):
                loss -= log_prob * R

            # Check for NaNs in loss
            if torch.isnan(loss):
                print(f"Episode {episode}, NaN in loss.")
                continue

        optimizer.zero_grad()
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)  # Gradient clipping
        optimizer.step()

        episode_cnt += 1
        total_reward += sum(rewards)
        total_steps += len(rewards)
        t2 = time.time()
        if episode % 1 == 0:
            print(f"Episode {episode}, loss:{loss.item():.4f}, {'succeed' if success else 'fail'}, steps:{len(rewards)}, total reward:{sum(rewards):.4f}, {t2-t1} sec")

if __name__ == "__main__":
    train(verbose=False)


/home/mcwave/.local/lib/python3.10/site-packages/torch/nn/modules/transformer.py:282: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(f"enable_nested_tensor is True, but self.use_nested_tensor is False because {why_not_sparsity_fast_path}")


Episode 0, loss:-4.8863, fail, steps:1, total reward:-10.0000, 0.37682557106018066 sec
Episode 1, loss:-97.2770, fail, steps:55, total reward:-10.7000, 0.3229947090148926 sec
Episode 2, loss:-125.7638, fail, steps:195, total reward:-16.2000, 1.3679430484771729 sec
Episode 3, loss:-139.7284, fail, steps:352, total reward:-17.5000, 1.9950463771820068 sec
Episode 4, loss:-76.8349, fail, steps:385, total reward:-10.7000, 2.3606679439544678 sec
Episode 5, loss:-81.9912, fail, steps:384, total reward:-11.7000, 2.414405584335327 sec
Episode 6, loss:-80.5492, fail, steps:385, total reward:-11.6000, 2.397667169570923 sec
Episode 7, loss:-86.3087, fail, steps:384, total reward:-13.7000, 2.670753002166748 sec
Episode 8, loss:-78.5785, fail, steps:385, total reward:-13.0000, 2.367225408554077 sec
Episode 9, loss:-94.7922, fail, steps:385, total reward:-13.8000, 2.42891526222229 sec
Episode 10, loss:-42.3073, fail, steps:386, total reward:-8.7000, 2.3523802757263184 sec
Episode 11, loss:-52.2497, f

Episode 94, loss:11.0427, fail, steps:388, total reward:5.7000, 2.287523031234741 sec
Episode 95, loss:22.6288, fail, steps:389, total reward:7.6000, 2.2127790451049805 sec
Episode 96, loss:46.5157, fail, steps:390, total reward:13.9000, 2.4900965690612793 sec
Episode 97, loss:23.2606, fail, steps:390, total reward:10.6000, 2.5361812114715576 sec
Episode 98, loss:17.9773, fail, steps:389, total reward:7.7000, 2.495478630065918 sec
Episode 99, loss:4.1719, fail, steps:388, total reward:5.4000, 2.4881961345672607 sec
Episode 100, loss:0.5171, fail, steps:387, total reward:2.5000, 2.4116764068603516 sec
Episode 101, loss:42.1526, fail, steps:390, total reward:12.9000, 2.4240410327911377 sec
Episode 102, loss:84.4600, fail, steps:393, total reward:21.2000, 2.5802197456359863 sec
Episode 103, loss:37.0380, fail, steps:390, total reward:11.3000, 2.6325478553771973 sec
Episode 104, loss:-1.8603, fail, steps:388, total reward:3.6000, 2.4225401878356934 sec
Episode 105, loss:76.1080, fail, step

Episode 187, loss:31.4790, fail, steps:389, total reward:10.8000, 2.391103744506836 sec
Episode 188, loss:71.2408, succeed, steps:377, total reward:19.9000, 2.3247764110565186 sec
Episode 189, loss:74.7580, fail, steps:393, total reward:22.1000, 2.4050567150115967 sec
Episode 190, loss:63.4223, fail, steps:392, total reward:19.4000, 2.361013174057007 sec
Episode 191, loss:78.6767, fail, steps:392, total reward:21.0000, 2.4871158599853516 sec
Episode 192, loss:65.1848, fail, steps:391, total reward:19.0000, 2.847322940826416 sec
Episode 193, loss:-41.4776, fail, steps:321, total reward:3.1000, 2.118692398071289 sec
Episode 194, loss:35.8201, fail, steps:390, total reward:11.8000, 2.536348581314087 sec
Episode 195, loss:100.1772, fail, steps:394, total reward:28.2000, 2.4428162574768066 sec
Episode 196, loss:33.8848, fail, steps:390, total reward:11.9000, 2.3797640800476074 sec
Episode 197, loss:32.7688, fail, steps:389, total reward:10.5000, 2.370093584060669 sec
Episode 198, loss:36.60

Episode 280, loss:59.1261, fail, steps:391, total reward:19.0000, 2.340878963470459 sec
Episode 281, loss:32.2211, fail, steps:390, total reward:12.4000, 2.425124406814575 sec
Episode 282, loss:55.9872, succeed, steps:388, total reward:19.0000, 2.763667345046997 sec
Episode 283, loss:66.9439, fail, steps:392, total reward:21.0000, 2.419142007827759 sec
Episode 284, loss:83.3242, fail, steps:393, total reward:23.3000, 2.384441375732422 sec
Episode 285, loss:111.8338, fail, steps:395, total reward:32.3000, 2.339660167694092 sec
Episode 286, loss:98.7905, fail, steps:394, total reward:29.3000, 2.390561819076538 sec
Episode 287, loss:45.3114, fail, steps:390, total reward:13.6000, 2.4262654781341553 sec
Episode 288, loss:60.1215, fail, steps:392, total reward:20.0000, 2.4757089614868164 sec
Episode 289, loss:77.0757, fail, steps:393, total reward:24.2000, 2.4841244220733643 sec
Episode 290, loss:103.3506, fail, steps:393, total reward:27.0000, 2.389275550842285 sec
Episode 291, loss:69.925

...

Episode 50384, loss:1.9997, fail, steps:392, total reward:21.2000, 2.311647653579712 sec
Episode 50385, loss:1.3086, succeed, steps:376, total reward:26.7000, 2.3760263919830322 sec
Episode 50386, loss:16.8471, succeed, steps:342, total reward:26.5000, 2.160829782485962 sec
Episode 50387, loss:9.1591, succeed, steps:293, total reward:33.1000, 1.8940963745117188 sec
Episode 50388, loss:9.0116, fail, steps:395, total reward:32.3000, 2.380376100540161 sec
Episode 50389, loss:18.8007, fail, steps:393, total reward:24.1000, 2.4740116596221924 sec
Episode 50390, loss:7.6808, fail, steps:394, total reward:27.8000, 2.6605451107025146 sec
Episode 50391, loss:2.9185, succeed, steps:380, total reward:21.4000, 2.2971205711364746 sec
Episode 50392, loss:8.2585, fail, steps:394, total reward:28.1000, 2.4010019302368164 sec
Episode 50393, loss:5.9187, succeed, steps:356, total reward:28.4000, 2.3022477626800537 sec
Episode 50394, loss:13.7531, fail, steps:396, total reward:37.2000, 2.3924107551574707

Episode 50475, loss:8.3796, fail, steps:395, total reward:35.4000, 2.488043785095215 sec
Episode 50476, loss:7.1727, fail, steps:393, total reward:26.7000, 2.416840076446533 sec
Episode 50477, loss:15.2408, fail, steps:394, total reward:31.3000, 2.4299569129943848 sec
Episode 50478, loss:4.6989, fail, steps:393, total reward:24.0000, 2.8726930618286133 sec
Episode 50479, loss:7.4643, succeed, steps:382, total reward:26.5000, 2.419020414352417 sec
Episode 50480, loss:8.5428, succeed, steps:273, total reward:16.6000, 1.7356011867523193 sec
Episode 50481, loss:5.0995, fail, steps:390, total reward:14.2000, 2.243250846862793 sec
Episode 50482, loss:8.5181, fail, steps:395, total reward:33.4000, 2.4300966262817383 sec
Episode 50483, loss:1.5865, succeed, steps:346, total reward:12.2000, 2.2327489852905273 sec
Episode 50484, loss:9.9173, succeed, steps:391, total reward:23.1000, 2.3712308406829834 sec
Episode 50485, loss:3.8722, fail, steps:393, total reward:26.1000, 2.2804670333862305 sec
E

Episode 50566, loss:5.1067, fail, steps:393, total reward:27.0000, 2.4785711765289307 sec
Episode 50567, loss:2.4919, fail, steps:394, total reward:29.4000, 2.4326236248016357 sec
Episode 50568, loss:3.6439, succeed, steps:340, total reward:21.1000, 2.0890185832977295 sec
Episode 50569, loss:6.6553, fail, steps:392, total reward:21.1000, 2.3949129581451416 sec
Episode 50570, loss:5.6654, fail, steps:396, total reward:36.4000, 2.4248814582824707 sec
Episode 50571, loss:8.2657, fail, steps:394, total reward:30.1000, 2.40620756149292 sec
Episode 50572, loss:3.1416, fail, steps:392, total reward:22.8000, 2.446937084197998 sec
Episode 50573, loss:5.8280, succeed, steps:269, total reward:28.2000, 1.8218870162963867 sec
Episode 50574, loss:7.4311, fail, steps:398, total reward:46.5000, 2.404977798461914 sec
Episode 50575, loss:3.7796, fail, steps:393, total reward:27.2000, 2.504633665084839 sec
Episode 50576, loss:5.9701, succeed, steps:298, total reward:22.8000, 1.8922159671783447 sec
Episod

Episode 50657, loss:5.5418, fail, steps:394, total reward:28.2000, 2.3256282806396484 sec
Episode 50658, loss:2.4975, fail, steps:393, total reward:27.0000, 2.3553709983825684 sec
Episode 50659, loss:8.2215, fail, steps:393, total reward:26.2000, 2.394774913787842 sec
Episode 50660, loss:6.1520, fail, steps:393, total reward:24.3000, 2.473496913909912 sec
Episode 50661, loss:5.0143, fail, steps:395, total reward:34.4000, 2.4307520389556885 sec
Episode 50662, loss:5.9042, fail, steps:395, total reward:32.3000, 2.377253293991089 sec
Episode 50663, loss:3.2233, succeed, steps:291, total reward:25.2000, 1.8659183979034424 sec
Episode 50664, loss:1.2282, fail, steps:393, total reward:26.2000, 2.4227304458618164 sec
Episode 50665, loss:4.1100, fail, steps:395, total reward:33.4000, 2.4067461490631104 sec
Episode 50666, loss:5.6027, fail, steps:396, total reward:37.0000, 2.4295291900634766 sec
Episode 50667, loss:1.4270, fail, steps:392, total reward:23.1000, 2.426126480102539 sec
Episode 506

Episode 50748, loss:9.3002, succeed, steps:353, total reward:28.5000, 2.142484188079834 sec
Episode 50749, loss:3.1232, fail, steps:392, total reward:23.1000, 2.405750036239624 sec
Episode 50750, loss:6.6780, succeed, steps:261, total reward:26.3000, 1.7067160606384277 sec
Episode 50751, loss:4.3988, fail, steps:394, total reward:29.9000, 2.6683883666992188 sec
Episode 50752, loss:10.3168, fail, steps:391, total reward:18.0000, 2.4197158813476562 sec
Episode 50753, loss:7.5518, fail, steps:393, total reward:24.1000, 2.331303834915161 sec
Episode 50754, loss:10.2577, fail, steps:396, total reward:36.3000, 2.3758575916290283 sec
Episode 50755, loss:3.5935, fail, steps:391, total reward:17.8000, 2.3715360164642334 sec
Episode 50756, loss:1.1949, fail, steps:392, total reward:22.1000, 2.542590856552124 sec
Episode 50757, loss:0.1105, fail, steps:390, total reward:11.8000, 2.3984405994415283 sec
Episode 50758, loss:12.6062, fail, steps:394, total reward:29.0000, 2.3484039306640625 sec
Episo